In [387]:
import pandas as pd
import re
import nltk
from nltk.tokenize import sent_tokenize, word_tokenize
from pymorphy3 import MorphAnalyzer
from nltk.corpus import stopwords
import numpy as np
import torch.nn as nn
from sklearn.model_selection import train_test_split
import torch

In [388]:
stopwords = stopwords.words('russian')

In [389]:
df = pd.read_csv('./data/Petitions.csv')
df

id                               public_petition_text  \
0      3168490                                     снег на дороге   
1      3219678                очистить кабельный киоск от рекламы   
2      2963920  Просим убрать все деревья и кустарники, которы...   
3      3374910  Неудовлетворительное состояние парадной - надп...   
4      3336285                                           Граффити   
...        ...                                                ...   
59884  3128111                           прошу закрасить граффити   
59885  3276713       Прошу вас отремонтировать пешеходную дорожку   
59886  3274663  Необходимо демонтировать незаконную рекламную ...   
59887  3359308  Очень гремит на ветру металлическая часть окна...   
59888  3209098  Две проблемы в одном:\n1) Незаконные надписи/о...   

                                         reason_category  
0                                        Благоустройство  
1                                        Благоустройство  
2                                        Благоустройство  
3                                         Содержание МКД  
4                                        Благоустройство  
...                                                  ...  
59884                                    Благоустройство  
59885                                    Благоустройство  
59886  Незаконная информационная и (или) рекламная ко...  
59887                                             Кровля  
59888                                    Благоустройство  

[59889 rows x 3 columns]

In [390]:
print(len(df['reason_category'].unique()), "\n", df['reason_category'].value_counts())

15 
 reason_category
Благоустройство                                                                     34769
Содержание МКД                                                                      14461
Нарушение правил пользования общим имуществом                                        2170
Незаконная информационная и (или) рекламная конструкция                              1831
Фасад                                                                                1483
Повреждения или неисправность элементов уличной инфраструктуры                       1164
Кровля                                                                                825
Водоснабжение                                                                         809
Состояние рекламных или информационных конструкций                                    673
Санитарное состояние                                                                  434
Центральное отопление                                                          

In [391]:
df.drop(columns="id", inplace=True)

In [392]:
new_df = df.sample(100)
new_df

public_petition_text  \
53750                           рисунки на фасаде здания   
37590  Разрушение асфальтобетонного покрытия на внутр...   
34507  Требуются очистить детскую площадку от снежног...   
4864   Вблизи детской площадки из земли торчит Проф. ...   
9075                                     мусор на дороге   
...                                                  ...   
16957       на торце дома  25 со стороны 21 дома надпись   
35870                       Мусор у дерева, прошу убрать   
25189                                    не очищена урна   
31748  Изрисован автобус дпс на детской площадке у Бо...   
56185                                   Мусор в парадной   

                                         reason_category  
53750                                    Благоустройство  
37590  Повреждения или неисправность элементов улично...  
34507                                    Благоустройство  
4864                                     Благоустройство  
9075                                     Благоустройство  
...                                                  ...  
16957                                    Благоустройство  
35870                                    Благоустройство  
25189                                    Благоустройство  
31748                                    Благоустройство  
56185                                     Содержание МКД  

[100 rows x 2 columns]

In [393]:
X = new_df["public_petition_text"].to_list()
y = new_df["reason_category"].to_list()

In [394]:
text1 = ['<p> Привет, чурка! Также Я: любл%ю тебя; и был @$, но не ты дурак</p>', 'Привет, чурка, я в Дубае']

In [395]:
# html_tag=re.compile('<.*?>')
# text = html_tag.sub('', text)
# text

In [396]:
def preprocessing_text(text):
    lst = []
    #remove html
    for i in text:
        html_tag=re.compile('<.*?>')
        text_no_html = html_tag.sub('', i)
        #remove quots
        text_only_letters = re.sub('[^\w\s]', '', text_no_html)
        #tokenizим
        words = word_tokenize(text_only_letters)
        #morphим
        morph = MorphAnalyzer()
        lemmas = [morph.normal_forms(w)[0] for w in words]
        #del_sw
        prepared = [w for w in lemmas if w not in stopwords]
        lemm_sentce = ' '.join(prepared)
        lst.append(lemm_sentce)
        # lst.append(prepared)
    return lst


In [397]:
prepro_text = preprocessing_text(text=X)
print(len(prepro_text))
prepro_text

100


['рисунок фасад здание',
 'разрушение асфальтобетонный покрытие внутридомовый дорога 5м 6м подъезд двухметровый рейка сантиметр пользоваться думаться всё понятно край глубина порядок 50 мм центр 100120 мм просить произвести ямочный ремонт ссылка температура ниже 5 градус считать отговорка',
 'требоваться очистить детский площадка снежный покров',
 'вблизи детский площадка земля торчать проф труба человек ходить запинаться',
 'мусор дорога',
 'убрать мусор около мусоропровод рядом почтовый ящик лежать третий неделя вымыть подъед 17',
 'мусор детский площадка',
 '1 парадный щиток слева вход надпись давно закрашиваться ук табличка парадный',
 'прогнить порог 2й дверь парадный входной дверь парадный порог разрушаеться образовать зазор окно дыра окно полностью закрываеться сильно продувать ветер стена этаж грязный чёрный пятно устранение необходимо осмотреть всё стена весь этаж тк фото весь грязный стена загрузить изз ограничение количество фото',
 'пр энтузиаст далее 53 38 10 парадный ремо

In [398]:
def del_word_len_one(list_w):
    w_del = []
    for i in range(0, len(list_w)):
        if len(list_w[i].split()) < 3:
            w_del.append(i)
    for index in sorted(w_del, reverse=True):
        del list_w[index]
        
    return list_w

In [416]:
new_prepro_text = del_word_len_one(prepro_text)
len(new_prepro_text)
new_prepro_text

['рисунок фасад здание',
 'разрушение асфальтобетонный покрытие внутридомовый дорога 5м 6м подъезд двухметровый рейка сантиметр пользоваться думаться всё понятно край глубина порядок 50 мм центр 100120 мм просить произвести ямочный ремонт ссылка температура ниже 5 градус считать отговорка',
 'требоваться очистить детский площадка снежный покров',
 'вблизи детский площадка земля торчать проф труба человек ходить запинаться',
 'убрать мусор около мусоропровод рядом почтовый ящик лежать третий неделя вымыть подъед 17',
 'мусор детский площадка',
 '1 парадный щиток слева вход надпись давно закрашиваться ук табличка парадный',
 'прогнить порог 2й дверь парадный входной дверь парадный порог разрушаеться образовать зазор окно дыра окно полностью закрываеться сильно продувать ветер стена этаж грязный чёрный пятно устранение необходимо осмотреть всё стена весь этаж тк фото весь грязный стена загрузить изз ограничение количество фото',
 'пр энтузиаст далее 53 38 10 парадный ремонт покраска почто

In [400]:
# for i in range(0, 5):
#     print(prepro_text[i], len(prepro_text[i].split()))
for i in range(0, 5):
    for j in range(0, len(prepro_text[i].split()) - 1):
        words_need = (prepro_text[i].split())[j]


# prepro_text[0].split()

In [401]:
count_vocab = set((' '.join(prepro_text).split()))
word_to_ix = {word: i for i, word in enumerate(count_vocab)}
word_to_ix

{'контролироваться': 0,
 'ветер': 1,
 'апрель': 2,
 'знать': 3,
 'привести': 4,
 'компания': 5,
 'травмирование': 6,
 'отслоение': 7,
 'мост': 8,
 'неоднократно': 9,
 'лифт': 10,
 'дорога': 11,
 'замок': 12,
 'человек': 13,
 'видеть': 14,
 'надлежащий': 15,
 'ссылка': 16,
 'давно': 17,
 'однако': 18,
 'территорииа': 19,
 'понятно': 20,
 '9': 21,
 'фонарь': 22,
 'отличаться': 23,
 'какойтый': 24,
 'крупногабаритный': 25,
 'течение': 26,
 'согласно': 27,
 'образоваться': 28,
 'прогнить': 29,
 'продувать': 30,
 'бетонный': 31,
 'захлопнуть': 32,
 'район': 33,
 'законность': 34,
 'ещё': 35,
 'машина': 36,
 'необходимо': 37,
 'свисать': 38,
 'текущий': 39,
 'рисунок': 40,
 'одежда': 41,
 'продажа': 42,
 'какимитый': 43,
 'включить': 44,
 'поребрик': 45,
 'заплатка': 46,
 'остаток': 47,
 'остановка': 48,
 'ук': 49,
 'дом': 50,
 '2ий': 51,
 'счёт': 52,
 'открыть': 53,
 'выход': 54,
 '3318379': 55,
 'сломать': 56,
 '5': 57,
 'лампочка': 58,
 'самовольный': 59,
 'проверить': 60,
 'подъед': 61,


In [402]:
word_list = list(word_to_ix.keys())
word_list

['контролироваться',
 'ветер',
 'апрель',
 'знать',
 'привести',
 'компания',
 'травмирование',
 'отслоение',
 'мост',
 'неоднократно',
 'лифт',
 'дорога',
 'замок',
 'человек',
 'видеть',
 'надлежащий',
 'ссылка',
 'давно',
 'однако',
 'территорииа',
 'понятно',
 '9',
 'фонарь',
 'отличаться',
 'какойтый',
 'крупногабаритный',
 'течение',
 'согласно',
 'образоваться',
 'прогнить',
 'продувать',
 'бетонный',
 'захлопнуть',
 'район',
 'законность',
 'ещё',
 'машина',
 'необходимо',
 'свисать',
 'текущий',
 'рисунок',
 'одежда',
 'продажа',
 'какимитый',
 'включить',
 'поребрик',
 'заплатка',
 'остаток',
 'остановка',
 'ук',
 'дом',
 '2ий',
 'счёт',
 'открыть',
 'выход',
 '3318379',
 'сломать',
 '5',
 'лампочка',
 'самовольный',
 'проверить',
 'подъед',
 'основное',
 '1860005',
 'несоответствие',
 'выбоина',
 'провалиться',
 'ограждение',
 'ботанический',
 'город',
 '20182020',
 'красный',
 'пожалуйста',
 'обработка',
 'личность',
 'поток',
 'ас',
 'коллонтай',
 '3110прилагаться',
 'мусо

In [403]:
with open('word_list3.tsv', 'w', encoding='utf-8') as f:
    f.write('\n'.join(word_list))

In [404]:
def embedding_matrix(f):
    count_vocab = set((' '.join(f).split()))
    print(len(count_vocab))
    word_to_ix = {word: i for i, word in enumerate(count_vocab)}
    print(word_to_ix)
    a = max(word_to_ix.values()) + 1
    print(a)
    matrica = [[0] * a for _ in range(a)]
    for k in range(0, len(f)):
        b = len(f[k].split())
        words = f[k].split()
        for i in range(b):
            for j in range(i+1, b):
                if words[i] in f[k] and words[j] in f[k]:
                    matrica[word_to_ix[words[i]]][word_to_ix[words[j]]] += 1
                    matrica[word_to_ix[words[j]]][word_to_ix[words[i]]] += 1

    # for row in matrica:
    #     print(row)
    
    return matrica

In [405]:
emb_matr = embedding_matrix(prepro_text)
emb_matr

617
{'контролироваться': 0, 'ветер': 1, 'апрель': 2, 'знать': 3, 'привести': 4, 'компания': 5, 'травмирование': 6, 'отслоение': 7, 'мост': 8, 'неоднократно': 9, 'лифт': 10, 'дорога': 11, 'замок': 12, 'человек': 13, 'видеть': 14, 'надлежащий': 15, 'ссылка': 16, 'давно': 17, 'однако': 18, 'территорииа': 19, 'понятно': 20, '9': 21, 'фонарь': 22, 'отличаться': 23, 'какойтый': 24, 'крупногабаритный': 25, 'течение': 26, 'согласно': 27, 'образоваться': 28, 'прогнить': 29, 'продувать': 30, 'бетонный': 31, 'захлопнуть': 32, 'район': 33, 'законность': 34, 'ещё': 35, 'машина': 36, 'необходимо': 37, 'свисать': 38, 'текущий': 39, 'рисунок': 40, 'одежда': 41, 'продажа': 42, 'какимитый': 43, 'включить': 44, 'поребрик': 45, 'заплатка': 46, 'остаток': 47, 'остановка': 48, 'ук': 49, 'дом': 50, '2ий': 51, 'счёт': 52, 'открыть': 53, 'выход': 54, '3318379': 55, 'сломать': 56, '5': 57, 'лампочка': 58, 'самовольный': 59, 'проверить': 60, 'подъед': 61, 'основное': 62, '1860005': 63, 'несоответствие': 64, 'выб

[[0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  1,
  2,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  2,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  1,
  0,
  0,
  0,
  0,
  2,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  2,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  1,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  2,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,


In [406]:
from sklearn.decomposition import PCA

In [407]:
pca = PCA(n_components=30)
pca.fit(emb_matr)
data_pca = pca.transform(emb_matr)

In [408]:
np.savetxt('embeddings.tsv', data_pca, delimiter='\t')

## Neural_buri

In [409]:
count_vocab2 = set((' '.join(prepro_text).split()))
print(len(count_vocab2))
word_to_ix2 = {word: i for i, word in enumerate(count_vocab2)}
word_to_ix2

617


{'контролироваться': 0,
 'ветер': 1,
 'апрель': 2,
 'знать': 3,
 'привести': 4,
 'компания': 5,
 'травмирование': 6,
 'отслоение': 7,
 'мост': 8,
 'неоднократно': 9,
 'лифт': 10,
 'дорога': 11,
 'замок': 12,
 'человек': 13,
 'видеть': 14,
 'надлежащий': 15,
 'ссылка': 16,
 'давно': 17,
 'однако': 18,
 'территорииа': 19,
 'понятно': 20,
 '9': 21,
 'фонарь': 22,
 'отличаться': 23,
 'какойтый': 24,
 'крупногабаритный': 25,
 'течение': 26,
 'согласно': 27,
 'образоваться': 28,
 'прогнить': 29,
 'продувать': 30,
 'бетонный': 31,
 'захлопнуть': 32,
 'район': 33,
 'законность': 34,
 'ещё': 35,
 'машина': 36,
 'необходимо': 37,
 'свисать': 38,
 'текущий': 39,
 'рисунок': 40,
 'одежда': 41,
 'продажа': 42,
 'какимитый': 43,
 'включить': 44,
 'поребрик': 45,
 'заплатка': 46,
 'остаток': 47,
 'остановка': 48,
 'ук': 49,
 'дом': 50,
 '2ий': 51,
 'счёт': 52,
 'открыть': 53,
 'выход': 54,
 '3318379': 55,
 'сломать': 56,
 '5': 57,
 'лампочка': 58,
 'самовольный': 59,
 'проверить': 60,
 'подъед': 61,


In [410]:
lookup = {value: key for key, value in word_to_ix2.items()}
lookup

{0: 'контролироваться',
 1: 'ветер',
 2: 'апрель',
 3: 'знать',
 4: 'привести',
 5: 'компания',
 6: 'травмирование',
 7: 'отслоение',
 8: 'мост',
 9: 'неоднократно',
 10: 'лифт',
 11: 'дорога',
 12: 'замок',
 13: 'человек',
 14: 'видеть',
 15: 'надлежащий',
 16: 'ссылка',
 17: 'давно',
 18: 'однако',
 19: 'территорииа',
 20: 'понятно',
 21: '9',
 22: 'фонарь',
 23: 'отличаться',
 24: 'какойтый',
 25: 'крупногабаритный',
 26: 'течение',
 27: 'согласно',
 28: 'образоваться',
 29: 'прогнить',
 30: 'продувать',
 31: 'бетонный',
 32: 'захлопнуть',
 33: 'район',
 34: 'законность',
 35: 'ещё',
 36: 'машина',
 37: 'необходимо',
 38: 'свисать',
 39: 'текущий',
 40: 'рисунок',
 41: 'одежда',
 42: 'продажа',
 43: 'какимитый',
 44: 'включить',
 45: 'поребрик',
 46: 'заплатка',
 47: 'остаток',
 48: 'остановка',
 49: 'ук',
 50: 'дом',
 51: '2ий',
 52: 'счёт',
 53: 'открыть',
 54: 'выход',
 55: '3318379',
 56: 'сломать',
 57: '5',
 58: 'лампочка',
 59: 'самовольный',
 60: 'проверить',
 61: 'подъед',


In [411]:
num_emb = list(lookup.keys())
len(num_emb)

617

In [412]:
embs = nn.Embedding(len(num_emb), 3)
input = torch.tensor(num_emb)

In [413]:
import torch.nn.functional as F

In [414]:
def generate_context_word_pairs(corpus, window_size, vocab_size):
    context_length = window_size*2
    # (prepro_text[0].split())[0]
    for words in corpus[words]:
        print(words)
        sentence_length = len(corpus)
        print(sentence_length)
        for index, word in enumerate(corpus):
            context_words = []
            label_word = []
            start = index - window_size

            # end = index + window_size + 1
            # context_words.append([corpus[i] for i in range(start, end) if 0 <= i < sentence_length and i != index])
            # label_word.append(word)
            # print(context_words)
            # print(label_word)
            # x = context_words
            # y = label_word, vocab_size
            # yield (x, y)
            return 0

In [415]:
generate_context_word_pairs(word_list, 4, len(count_vocab2))

UnboundLocalError: cannot access local variable 'words' where it is not associated with a value

In [ ]:
class CBOWModeler(nn.Module):

    def __init__(self, vocab_size, embedding_dim, context_size):
        super(CBOWModeler, self).__init__()
        self.embeddings = nn.Embedding(vocab_size, embedding_dim)
        self.linear1 = nn.Linear(context_size * embedding_dim, 250)
        self.linear2 = nn.Linear(250, vocab_size)

    def forward(self, inputs):
        embeds = self.embeddings(inputs).view((1, -1))
        out1 = F.relu(self.linear1(embeds))
        out2 = self.linear2(out1)           
        log_probs = F.log_softmax(out2, dim=1)
        return log_probs

    # def predict(self,input):
    #     context_idxs = torch.tensor([word_to_ix2[w] for w in input], dtype=torch.long)
    #     res = self.forward(context_idxs)
    #     # res_arg = torch.argmax(res)
    #     res_val, res_ind = res.sort(descending=True)
    #     res_val = res_val[0][:5]
    #     res_ind = res_ind[0][:5]
    #     #print(res_val)
    #     #print(res_ind)
    #     for arg in zip(res_val,res_ind):
    #         #print(arg)
    #         print([(key,val,arg[0]) for key,val in word_to_ix2.items() if val == arg[1]])

In [ ]:
loss_function = nn.NLLLoss()

In [ ]:
model = CBOWModeler(len(num_emb), 10, 3)
model

CBOWModeler(
  (embeddings): Embedding(595, 10)
  (linear1): Linear(in_features=30, out_features=250, bias=True)
  (linear2): Linear(in_features=250, out_features=595, bias=True)
)

In [ ]:
optimizer = torch.optim.SGD(model.parameters(), lr=0.001)

In [ ]:
wordvecs = model.linear2.weight.cpu().detach().numpy()
wordvecs

array([[ 0.0251831 , -0.02891936, -0.03031075, ...,  0.03528842,
        -0.03260382,  0.03102396],
       [ 0.05762857, -0.05076442, -0.04819339, ..., -0.00330954,
         0.05132478,  0.017945  ],
       [ 0.04069733, -0.01938121, -0.05274904, ...,  0.02470092,
        -0.04803883,  0.04907109],
       ...,
       [-0.0528859 , -0.01634015,  0.03947989, ..., -0.01430494,
         0.04670191,  0.0130012 ],
       [-0.05101476, -0.01645047, -0.01007505, ...,  0.00647969,
         0.01355693,  0.00826564],
       [ 0.00495719,  0.05280975, -0.0389386 , ...,  0.03492624,
         0.00658961,  0.03668834]], dtype=float32)

In [ ]:
np.savetxt('word2vec_vectors.tsv', wordvecs, delimiter='\t')

In [ ]:
dframe['X'][0].split()

['двор',
 'дом',
 'арка',
 'свальный',
 'крупногабаритный',
 'мусор',
 'большой',
 'количество',
 'картонный',
 'коробка',
 'xxxxxxxxxxxxx',
 'xxxxxx',
 'xxxxxxxxxx',
 'x',
 'xxxxxxxxxxxxx',
 'xxxxxxxxxxx',
 'сегодняшний',
 'день',
 '03042021',
 'мусор',
 'убрать',
 'количество',
 'увеличиться',
 'проблема',
 'устранить']

In [ ]:
epochs = 5

loss_values = []
for epoch in range(epochs):
    for x_b, y_b in train_dl:

        outputs = model(x_b)

        loss_value = loss_function(outputs, y_b)

        loss_value.backward()

        optimizer.step()

        optimizer.zero_grad()
    loss_values.append(loss_value.item())

    print(f'Эпоха {epoch + 1}, Значение функции потерь: {loss_value.item()}')